# Alpha Beta Filter Dashboard

Filecoin implements a Alpha Beta Filter for estimating the Block Reward 
and the QA Network Power on the Sector Initial Pledge Calculations.

- Sector Pledge = Storage Pledge + Consensus Pledge
- Initial Storage Pledge = Estimate of 20 Days of Block Reward
- Initial Consensus Pledge = 30% * Total Circulating Supply * Sector QA Power / max(Baseline Function , Estimate of QA Network Power)

Current parameters are:

- $\alpha=9.25e-4$
- $\beta= 2.84e-7$ per epoch

## References

### Source Code

- Alpha Beta Filter: https://github.com/filecoin-project/specs-actors/blob/f6a8d2a6f1573b2786cd573a2ea005aa04b1eb56/actors/util/smoothing/alpha_beta_filter.go#L78
- Reward Actor: https://github.com/filecoin-project/specs-actors/blob/f6a8d2a6f1573b2786cd573a2ea005aa04b1eb56/actors/builtin/reward/reward_state.go
- Power Actor: https://github.com/filecoin-project/specs-actors/blob/f6a8d2a6f1573b2786cd573a2ea005aa04b1eb56/actors/builtin/power/power_state.go#L298



## Setting-up

In [1]:
%load_ext autotime
%load_ext autoreload
%autoreload 2

time: 13 ms (started: 2021-08-23 12:49:14 -04:00)


In [2]:
# External depences
import pandas as pd
import numpy as np
import plotly.express as px

# Move path to parent folder
import sys
sys.path.insert(1, '../')

# Internal dependences
from filecoin_metrics.connection import get_connection, get_connection_string
from filecoin_metrics.metrics import *

time: 814 ms (started: 2021-08-23 12:49:15 -04:00)


In [3]:
conn_string = get_connection_string('../config/sentinel-conn-string.txt')
connection = get_connection(conn_string)
BASELINE_CROSSING = '2021-04-02 05:00+00'

time: 5.77 s (started: 2021-08-23 12:49:16 -04:00)


## Block Reward Estimator

In [4]:
QUERY = f"""
/* 
Retrieve block reward & qa network power daily averages / stdevs for
- Measurements
- Position Estimates
- Velocity Estimates
*/

select
    /* Timestamp */
	date_trunc('HOUR', to_timestamp(height_to_unix(cr.height))) as timestamp,

    /* Reward measurements & estimates */
    avg(cr.new_reward::numeric / 10^18) as reward_avg,
    stddev(cr.new_reward::numeric / 10^18) as reward_std,
	avg(cr.new_reward_smoothed_position_estimate::numeric / (2^128 * 10^18)) as reward_position_avg, /* FIL */
    stddev(cr.new_reward_smoothed_position_estimate::numeric / (2^128 * 10^18)) as reward_position_std, /* FIL */
    avg(cr.new_reward_smoothed_velocity_estimate::numeric / (2^128 * 10^18)) as reward_velocity_avg, /* FIL per epoch */
    stddev(cr.new_reward_smoothed_velocity_estimate::numeric / (2^128 * 10^18)) as reward_velocity_std, /* FIL per epoch */

    /* Power measurements & estimates */
    avg(cp.total_qa_bytes_power::numeric / 1024^5) as qa_power_avg, /* PiB */
    stddev(cp.total_qa_bytes_power::numeric / 1024^5) as qa_power_std, /* PiB */
	avg(cp.qa_smoothed_position_estimate::numeric / (2^128 * 1024^5)) as qa_power_position_avg, /* PiB */
    stddev(cp.qa_smoothed_position_estimate::numeric / (2^128 * 1024^5)) as qa_power_position_std, /* PiB */
    avg(cp.qa_smoothed_velocity_estimate::numeric / (2^128 * 1024^5)) as qa_power_velocity_avg, /* PiB per epoch */
    stddev(cp.qa_smoothed_velocity_estimate::numeric / (2^128 * 1024^5)) as qa_power_velocity_std /* PiB per epoch */
FROM chain_rewards cr
join chain_powers cp on cp.height = cr.height
where cr.height > 148888 /* Mainnet Launch Block Height */
group by timestamp
order by timestamp
"""

query_df = (pd.read_sql(QUERY, connection))

time: 3min 28s (started: 2021-08-23 12:49:22 -04:00)


In [14]:
fig = px.line(query_df, 
            x='timestamp',          
            y=['reward_avg', 'reward_position_avg'],
            title='Hourly Averages of Block Reward')
fig.show()

time: 458 ms (started: 2021-08-23 13:03:25 -04:00)


In [15]:
fig = px.line(query_df, 
            x='timestamp',          
            y=['reward_std', 'reward_position_std'],
            log_y=True,
            title='Hourly Standard Deviation of Block Rewards')
fig.show()

time: 370 ms (started: 2021-08-23 13:03:31 -04:00)


In [16]:
velocity_z = (query_df.reward_velocity_std / query_df.reward_velocity_avg).abs()

fig = px.line(query_df.assign(std_per_avg=velocity_z), 
            x='timestamp',          
            y='std_per_avg',
            log_y=True,
            title='Block Reward Velocity Hourly Standard Score')
fig.show()

time: 242 ms (started: 2021-08-23 13:03:48 -04:00)


In [17]:
relative_error = (query_df.reward_avg - query_df.reward_position_avg) / query_df.reward_avg
df = query_df.assign(relative_reward_error=relative_error)
fig = px.line(df,
            x='timestamp',
            y='relative_reward_error',
            title='Mean Relative Error on Hourly Averages of Block Rewards')
fig.update_layout(yaxis=dict(tickformat=".2%"))
fig.show()

time: 198 ms (started: 2021-08-23 13:03:51 -04:00)


### QA Network Power Estimator

In [18]:
fig = px.line(query_df, 
            x='timestamp',          
            y=['qa_power_avg', 'qa_power_position_avg'],
            title='Hourly  Averages of QA Power')
fig.show()

time: 433 ms (started: 2021-08-23 13:03:54 -04:00)


In [19]:
fig = px.line(query_df, 
            x='timestamp',          
            y=['qa_power_std', 'qa_power_position_std'],
            log_y=True,
            title='Hourly Standard Deviation of QA Power')
fig.show()

time: 393 ms (started: 2021-08-23 13:03:58 -04:00)


In [20]:
relative_error = (query_df.qa_power_avg - query_df.qa_power_position_avg) / query_df.qa_power_avg
df = query_df.assign(relative_reward_error=relative_error)
fig = px.line(df,
            x='timestamp',
            y='relative_reward_error',
            title='Mean Relative Error on Hourly Averages of QA Power')
fig.update_layout(yaxis=dict(tickformat=".1%"))
fig.show()

time: 203 ms (started: 2021-08-23 13:04:17 -04:00)


In [21]:
velocity_z = (query_df.qa_power_velocity_std / query_df.qa_power_velocity_avg).abs()

fig = px.line(query_df.assign(std_per_avg=velocity_z), 
            x='timestamp',          
            y='std_per_avg',
            log_y=True,
            title='QA Power Velocity Hourly Standard Score')
fig.show()

time: 219 ms (started: 2021-08-23 13:04:40 -04:00)
